In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
!pip install optuna optuna-dashboard
!pip install git+https://github.com/R-N/ml-utility-loss
!pip install git+https://github.com/R-N/ml-utility-loss --force-reinstall --no-deps

  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-0lvntdr8
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-0lvntdr8
  Resolved https://github.com/R-N/ml-utility-loss to commit 999fa9d4bdbb358553011a9c2171aded09814fc4
  Preparing metadata (setup.py) ... done
  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-yf3xds_g
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-yf3xds_g
  Resolved https://github.com/R-N/ml-utility-loss to commit 999fa9d4bdbb358553011a9c2171aded09814fc4
  Preparing metadata (setup.py) ... done
  Created wheel for ml-utility-loss: filename=ml_utility_loss-0.1.1-py3-none-any.whl size=377794 sha256=9b7126c41fb084aa428702d22bb7d3a3cf9182b8ca66b7d8af8a0f2e9ffa11d6
  Stored in directory: /tmp/pip-ephem-wheel-cache-n3qnkp_i/wheels/54/30/38/31c28079b5f07b6c793211d38f72e7f0be6764bfdfe016df74
Successfully buil

In [3]:
%cd /content
!curl -Ls https://github.com/ekzhang/bore/releases/download/v0.4.0/bore-v0.4.0-x86_64-unknown-linux-musl.tar.gz | tar zx -C /usr/bin
!curl -Lo /usr/bin/cloudflared https://github.com/cloudflare/cloudflared/releases/latest/download/cloudflared-linux-amd64 && chmod +x /usr/bin/cloudflared

/content
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100 34.7M  100 34.7M    0     0  28.6M      0  0:00:01  0:00:01 --:--:-- 49.8M


In [4]:
%cd /content
!rm -rf ml-utility-loss
!git clone https://github.com/R-N/ml-utility-loss
%cd ml-utility-loss
!rm -rf ml_utility_loss

/content
Cloning into 'ml-utility-loss'...
remote: Enumerating objects: 54414, done.
remote: Counting objects: 100% (7327/7327), done.
remote: Compressing objects: 100% (3252/3252), done.
remote: Total 54414 (delta 4134), reused 7251 (delta 4059), pack-reused 47087
Receiving objects: 100% (54414/54414), 239.42 MiB | 11.05 MiB/s, done.
Resolving deltas: 100% (6182/6182), done.
Updating files: 100% (50325/50325), done.
/content/ml-utility-loss


In [5]:
datasets = [
    "insurance",
    "treatment",
    "contraceptive"
]

model_dir = "/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/"

In [61]:
import pandas as pd
import numpy as np
import json
import os

dataset_dir = "datasets"
dataset_name = "insurance"

df = pd.read_csv(os.path.join(dataset_dir, f"{dataset_name}.csv"))
with open(os.path.join(dataset_dir, f"{dataset_name}.json")) as f:
    info = json.load(f)

In [62]:
from ml_utility_loss.util import split_df_ratio

task = info["task"]
target = info["target"]
cat_features = info["cat_features"]
mixed_features = info["mixed_features"]
longtail_features = info["longtail_features"]
integer_features = info["integer_features"]

dfs = {
    "df": df,
}
for i in range(5):
    train, test = split_df_ratio(df, ratio=0.2, i=i, seed=42)
    dfs[i] = train


In [83]:
from ml_utility_loss.util import mkdir

model_name = "lct_ae"
df_name = 4
#model_name_2 = f"{model_name}_{dataset_name}_{df_name}"
model_dir_2 = os.path.join(model_dir, model_name, dataset_name, str(df_name))
mkdir(model_dir_2)
model_path = os.path.join(model_dir_2, f"model.pt")
state_path = os.path.join(model_dir_2, f"state.json")
params_path = os.path.join(model_dir_2, f"params.json")

In [84]:
print(model_path)

/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/lct_ae/insurance/4/model.pt


In [85]:

from ml_utility_loss.tuning import create_objective
import ml_utility_loss.synthesizers.lct_gan.params as PARAMS
from ml_utility_loss.util import filter_dict_2

params = getattr(PARAMS, dataset_name).BEST
ae_params = filter_dict_2(params, PARAMS.default.AE_PARAMS)

dataset_kwargs={
    "categorical_columns": cat_features,
    "mixed_columns": mixed_features,
    "log_columns": longtail_features,
    "integer_columns": integer_features,
}

model_params={
    **ae_params,
    **dataset_kwargs,
}

In [86]:
from ml_utility_loss.synthesizers.lct_gan.pipeline import create_ae

ae, recon = create_ae(
    dfs[df_name],
    **model_params
)

/usr/local/lib/python3.10/dist-packages/sklearn/mixture/_base.py:274: ConvergenceWarning: Initialization 1 did not converge. Try different init parameters, or increase max_iter, tol or check for degenerate data.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/mixture/_base.py:274: ConvergenceWarning: Initialization 1 did not converge. Try different init parameters, or increase max_iter, tol or check for degenerate data.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/mixture/_base.py:119: ConvergenceWarning: Number of distinct clusters (6) found smaller than n_clusters (10). Possibly due to duplicate points in X.
  .fit(X)
/usr/local/lib/python3.10/dist-packages/sklearn/mixture/_base.py:274: ConvergenceWarning: Initialization 1 did not converge. Try different init parameters, or increase max_iter, tol or check for degenerate data.
  warnings.warn(
100%|██████████| 267/267 [00:23<00:00, 11.29it/s]


In [87]:
import torch
from copy import deepcopy
import json

!rm -rf params_path
!rm -rf model_path
!rm -rf state_path
torch.save(ae, model_path)
torch.save(deepcopy(ae.state_dict()), state_path)
with open(params_path, "w") as f:
    json.dump(model_params, f, indent=4)